## Example GPFS Workflow

This notebook aims to give an example GPFS workflow using an early version of the `rc_gpfs` package. This will start with a raw GPFS log file moving through stages for splitting and conversion to parquet using the Python API, although both steps could be done using the built-in CLI as well. Once the parquet dataset is created, it will create the basic `tld` summarized report on file count and storage use. From there, some example plots showing breakdowns of storage used by file age will be created.

This notebook assumes being run in a job with at least one GPU, although some options can be changed to use a CPU-only backend. A GPU is recommended for analyzing larger logs, such as for `/data/project`.

### Suggested Compute Resources

For analyzing a `/data/project` report, I suggest the following resources:

- ntasks = 2
- cpus-per-task = 32
- ntasks-per-socket = 1
- gres = gpu:2
- partition = amperenodes
- mem = 256G

When using more than 1 GPU, specifying 1 task per socket is highly recommended to guarantee matching the GPU socket socket affinity on the current A100 DGX. 

### Package and Input Setup

In [ ]:
from pathlib import Path

# Import the three main Python API submodules for analyzing a report
from rc_gpfs import process, policy
from rc_gpfs.report import plotting

In [ ]:
# File patch setup
gpfs_log_root = Path('/data/rc/gpfs-policy/data/list-policy_data-project_list-path-external_slurm-31035593_2025-01-05T00:00:24/')
raw_log = gpfs_log_root.joinpath('raw','list-policy_data-project_list-path-external_slurm-31035593_2025-01-05T00:00:24.gz')

### Log Preprocessing

This section shows how to use the `policy` module to split the large GPFS log into smaller parts and then convert each part to a separate parquet file for analysis elsewhere. You can specify different filepaths for the outputs of each stage if you want, but it's generally easier to let the functions use the standard log directory structure seen below:

``` text
.
└── log_root/
    ├── raw/
    │   └── raw_log.gz
    ├── chunks/
    │   ├── list-000.gz
    │   ├── list-001.gz
    │   └── ...
    ├── parquet/
    │   ├── list-000.parquet
    │   ├── list-001.parquet
    │   └── ...
    ├── reports/
    └── misc/
```

The directory structure will be automatically created as needed by each function. It's generally easier to not specify output paths for consistency in organization.

#### Split

In [ ]:
# Split raw log
policy.split(log=raw_log)

#### Convert

Opposed to split, it's much faster to submit the parquet conversion as an array job (built into the `cli` submodule), but it's possible to do here via the multiprocessing library as well.

In [ ]:
from multiprocessing import Pool
from rc_gpfs.utils import parse_scontrol

cores,_ = parse_scontrol()
split_files = list(gpfs_log_root.joinpath('chunks').glob('*.gz'))

In [ ]:
with Pool(cores) as pool:
    pool.map(policy.convert,split_files)

### Aggregate

In [ ]:
pq_path = gpfs_log_root.joinpath('parquet')
delta_vals = list(range(0,21,6))
delta_unit = 'M'
report_name = 'agg_by_tld_atime.parquet'

When choosing what sort of compute we want to use, we can let the package infer the backend based on the in-memory dataset size as well as the available compute resources, but it's easier in this case to specify that we want to use `dask_cuda`. Backend initialization happens later in the notebook

In [ ]:
# Compute backend setup
with_cuda = True
with_dask = True

In [ ]:
process.aggregate_gpfs_dataset(dataset_path=pq_path, delta_vals=delta_vals, delta_unit=delta_unit, report_name=report_name, with_cuda=with_cuda, with_dask=with_dask)

### Plotting

In [ ]:
import pandas as pd

In [ ]:
df = pd.read_parquet(gpfs_log_root.joinpath('reports',report_name))
df.columns = ['tld','dt_grp','bytes','file_count']
agg = df.groupby('dt_grp',observed=True)[['bytes','file_count']].sum().reset_index()

In [ ]:
exp,unit = plotting.choose_appropriate_storage_unit(agg['bytes'])
agg[unit] = agg['bytes']/(1024**exp)

In [ ]:
agg[['file_count_cum',f'{unit}_cum']] = agg[['file_count',unit]].cumsum()
agg[[unit,f'{unit}_cum']] = agg[[unit,f'{unit}_cum']].round(3)

In [ ]:
plotting.pareto_chart(agg,x='dt_grp',y=unit)